In [ ]:
# Companion Detection in DIVA+ Characterization Tables

This Jupyter notebook utilizes the `whereistheplanet` Python module to analyze DIVA+ characterization tables centered around specific stars. 
Its primary function is to identify potential companions.

## Criteria for Potential Companion Detection

To flag a detection as a potential companion, the following criteria are applied:

1. **Astrometric Consistency**: For each epoch, the detection's astrometry in DIVA+ must be within 0.5 FWHM-PSF of the astrometry predicted 
by the `whereistheplanet` module.

2. **Photometric Consistency**: If a detection satisfies the astrometric criterion, we further test if the mean difference in magnitude 
(`dmag`) across all wavelengths is consistent over all epochs. 
Specifically, the mean `dmag` at any given epoch must fall within the range of the overall mean 
`dmag` ± its standard deviation across all epochs.

## Limitations and Future Work

It is important to note that this software is designed for preliminary screening to quickly identify detections that may not correspond
to the intended companion. 
It should not be used to definitively classify a detection as a companion. 
A more detailed analysis, including the spectral type assessment of the detection, will be required for conclusive 
identification and is planned for future implementation in DIVA+.

In [ ]:
## Acknowledgment

If you use this notebook, you have to thanks wereistheplanet team  (see https://github.com/semaphoreP/whereistheplanet) 
and the DIVA+ team (https://hc-dc.cnrs.fr/acknowledgment/).

In [1]:
from astropy.table import Table
import pandas as pd
import os
import numpy as np
import subprocess
import re
import math

Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.


In [2]:
# path where you want to save results
path = ''

star_name = 'HIP_21547'  # Use DIVA+ name !
planet_name = '51erib' # whereismyplanet name !

# Instrument and algo used
#instr = 'IFS'
instr = 'IRDIS'

algo = 'TLOCI'
#algo = 'PCA'
#algo = 'PCApadova'
#algo = 'No_ADI'

# detection at each lambda having snr < snr_limit will be removed
snr_limit = 2
# detection at each lambda having dmag > dmag_limit will be removed
dmag_limit = 30
# detection at each lambda having err_dmag > err_dmag_limit will be removed
err_dmag_limit = 15

In [3]:
# Load a characterisations table from the DIVA+ URL (use Detections characterisations in the Search menu of DIVA+ to build it)
diva_table_url = "https://anis-dev.lam.fr/server/search/divap/characterisations?a=1;37;38;2;3;32;21;22;33;34;35;6;7;8;9;10;11;12;13;14;15;16;4;5&c=2::in::starname;34::in::instr;35::in::algo&f=csv"

# Replace the confs in the URL and load the table
diva_table_url = diva_table_url.replace('starname', star_name)
diva_table_url = diva_table_url.replace('instr', instr)
diva_table_url = diva_table_url.replace('algo', algo)

diva_table = Table.read(diva_table_url, format="csv")

# Convert the Astropy table to a Pandas DataFrame
diva_table_df = diva_table.to_pandas()

In [6]:
def average_by_detection_ids(df):

    if df.empty:
        raise ValueError('STOP: No detections for this instrument and reduction setup')
    else:
        # Select the necessary columns
        df = df[['star_name', 'observation_date', 'observation_mjd', 'wavelength', 'dra', 'err_dra', 'ddec', 'err_ddec',
                 'dmag', 'err_dmag', 'snr', 'detection_id']]

        # Print messages for removed rows
        removed_rows = df[(df['snr'] < snr_limit) | (df['dmag'] > dmag_limit) | (df['err_dmag'] > err_dmag_limit)]
        for index, row in removed_rows.iterrows():
            if row['snr'] < snr_limit:
                print(
                    f"The detection_id {row['detection_id']} has been removed at lambda = {row['wavelength']} because snr < " + str(snr_limit))
            elif row['dmag'] > dmag_limit:
                print(
                    f"The detection_id {row['detection_id']} has been removed at lambda = {row['wavelength']} because dmag > " + str(dmag_limit))
            elif row['err_dmag'] > err_dmag_limit:
                print(f"The detection_id {row['detection_id']} has been removed at lambda = {row['wavelength']} because err_dmag > " + str(err_dmag_limit))

        # Filter out rows based on snr and dmag and err_dmag conditions
        df = df[(df['snr'] >= snr_limit) & (df['dmag'] <= dmag_limit) & (df['err_dmag'] <= err_dmag_limit)]

    # Group the data by detection_id
    grouped = df.groupby('detection_id')

    # Check if each group has exactly one value of observation_mjd
    for name, group in grouped:
        if len(group['observation_mjd'].unique()) != 1:
            raise Exception(f"Le detection_id {name} a plus d'une valeur unique de observation_mjd.")

    # Calculate statistics for each group (mean on all the wavelenghts)
    stats_main = grouped.agg({
        'detection_id': 'first',
        'star_name': 'first',
        'observation_date': 'first',
        'observation_mjd': 'first',
        'dra': lambda x: 1000 * x.mean(),
        'err_dra': lambda x: 1000 * np.sqrt((x ** 2).sum()),
        'ddec': lambda x: 1000 * x.mean(),
        'err_ddec': lambda x: 1000 * np.sqrt((x ** 2).sum()),
        'dmag': lambda x: x.mean(),
        'err_dmag' : lambda x: np.sqrt((x ** 2).sum()),
        'snr': lambda x: x.mean()
    })

    # Calculate wavelength_min and wavelength_max
    stats_wave = grouped['wavelength'].agg([('wavelength_min', 'min'), ('wavelength_max', 'max')]) / 10000.

    # Combine the two dataframes
    stats = pd.concat([stats_main, stats_wave], axis=1)

    # Rename the columns
    stats.columns = ['detection_id', 'star_name', 'date', 'epoch', 'dra mean (mas)', 'sum_quad dra_err (mas)',
                     'ddec mean (mas)', ' sum_quad ddec_err (mas)', 'dmag', 'err_dmag', 'snr mean', 'wavelength_min', 'wavelength_max']
    # save in csv file
    #stats.to_csv(output_filename, index_label='detection_id')

    return stats

In [7]:
def check_detection_is_companion(path, table_detections, planet_name):

    distances = []
    list_fwhm_psf = []
    filtered_dmag_values = []
    filtered_err_dmag_values = []
    err_where_is_planet = []
    companion = []

    for index, row in table_detections.iterrows():
        observation_date = row['date']
        dra = row['dra mean (mas)']
        ddec = row['ddec mean (mas)']
        dmag = row['dmag']
        wavelength_max = row['wavelength_max']

        # FWHM_PSF computation
        fwhm_psf = (1.22 * wavelength_max * 1e-6 / 8.2) * (180 / np.pi) * 3600 * 1000
        list_fwhm_psf.append(fwhm_psf)

        # Search astrometry with whereisthepanet
        command = f"whereistheplanet {planet_name} --time {observation_date}"
        result = subprocess.run(command, shell=True, capture_output=True, text=True)

        # Extraction des offsets et des erreurs
        ra_offset, err_ra_offset = map(float, re.findall(r'RA Offset = ([-+]?\d+\.\d+) \+/- (\d+\.\d+) mas', result.stdout)[0])
        dec_offset, err_dec_offset = map(float, re.findall(r'Dec Offset = ([-+]?\d+\.\d+) \+/- (\d+\.\d+) mas', result.stdout)[0])

        err_radec_whereisplanet = np.sqrt(err_ra_offset**2 + err_dec_offset**2)
        err_where_is_planet.append(err_radec_whereisplanet)

        # Distance between whereisthepanet and DIVA+ astrometry
        distance = math.sqrt((ra_offset - dra) ** 2 + (dec_offset - ddec) ** 2)
        distances.append(distance)

        # select values where distance < 0.5 x FWHM_PSF (i.e. detections at position of the companion)
        if distance < fwhm_psf / 2:
            filtered_dmag_values.append(dmag)
            filtered_err_dmag_values.append(row['err_dmag'])

    # Compute dmag_moy and quadraticsum_err_dmag for detections selected
    if filtered_dmag_values:
        dmag_moy = np.mean(filtered_dmag_values)
        quadraticsum_err_dmag = np.sqrt(np.sum(np.array(filtered_err_dmag_values) ** 2))
    else:
        dmag_moy = np.nan
        quadraticsum_err_dmag = np.nan

    print('dmag mean on all the epochs of the potential companion: ', dmag_moy)
    print('quadratic sum of dmag errors on all the epochs of the potential companion:', quadraticsum_err_dmag)

    # Test the condition for each detection
    for distance, dmag, fwhm_psf in zip(distances, table_detections['dmag'], list_fwhm_psf):
        if (dmag_moy - quadraticsum_err_dmag <= dmag <= dmag_moy + quadraticsum_err_dmag) and (distance < fwhm_psf / 2):
            companion.append(True)
        else:
            companion.append(False)

    # add results in the DataFrame
    table_detections['FWHM_PSF (mas)'] = list_fwhm_psf
    table_detections['distance whereisplanet-diva (mas)'] = distances
    table_detections['err_where_is_planet'] = err_where_is_planet
    table_detections['companion'] = companion

    # Save the DataFrame in a CSV file
    output_file = os.path.join(path, f"{planet_name}_{instr}_{algo}_detection_companion.csv")
    table_detections.to_csv(output_file, index=False)

In [8]:
###########
###Main####
###########

diva_table_avg_by_detect_id = average_by_detection_ids(diva_table_df)

check_detection_is_companion(path, diva_table_avg_by_detect_id, planet_name)

The detection_id 269 has been removed at lambda = 16670 because snr < 2
dmag mean on all the epochs of the potential companion:  13.688
quadratic sum of dmag errors on all the epochs of the potential companion: 0.55
